In [1]:
!nvidia-smi

Thu Jul 11 17:37:15 2024       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 552.44                 Driver Version: 552.44         CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                     TCC/WDDM  | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 4060 ...  WDDM  |   00000000:01:00.0  On |                  N/A |
| N/A   46C    P8              1W /   80W |      87MiB /   8188MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [2]:
import os
import sys
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

import torch
import torch.nn as nn
import torch.optim as optim

import torchvision.utils
from torchvision import models
import torchvision.datasets as dsets
import torchvision.transforms as transforms
from torchsummary import summary

c:\Users\Dheeraj\AppData\Local\NVIDIA\MiniConda\envs\pytorch\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
from MedViT import MedViT_small as tiny
from MedViT import MedViT_base as base
from MedViT import MedViT_large as large

In [20]:
model = large()

initialize_weights...


In [21]:
model.proj_head[0]

Linear(in_features=1024, out_features=1000, bias=True)

In [22]:
checkpoint = torch.load('MedViT_large_im1k.pth')

In [23]:
model.load_state_dict(checkpoint['model'])

<All keys matched successfully>

In [24]:
model.proj_head[0] = torch.nn.Linear(in_features=1024, out_features=5, bias=True)

In [28]:
model = model.cuda()

In [26]:
print(checkpoint)

{'model': OrderedDict([('stem.0.conv.weight', tensor([[[[-0.0019,  0.0327, -0.0047],
          [ 0.0117,  0.0181, -0.1135],
          [ 0.0113,  0.0553, -0.0246]],

         [[-0.0004, -0.0328, -0.0216],
          [ 0.0079, -0.0481, -0.0607],
          [-0.0004, -0.0389, -0.0357]],

         [[-0.0006,  0.0255,  0.0034],
          [ 0.0049, -0.0030, -0.1000],
          [ 0.0088,  0.0568, -0.0315]]],


        [[[-0.0032, -0.0017, -0.0056],
          [-0.0057,  0.0108,  0.0027],
          [-0.0033,  0.0068,  0.0059]],

         [[ 0.0148,  0.0232,  0.0180],
          [ 0.0329,  0.0592,  0.0371],
          [ 0.0224,  0.0398,  0.0285]],

         [[-0.0151, -0.0249, -0.0136],
          [-0.0290, -0.0640, -0.0392],
          [-0.0195, -0.0435, -0.0347]]],


        [[[ 0.0221, -0.0077,  0.0017],
          [-0.0607,  0.0505,  0.0064],
          [-0.0132, -0.0132,  0.0142]],

         [[ 0.0038, -0.0331, -0.0114],
          [ 0.0033,  0.0951, -0.0547],
          [ 0.0164,  0.0022, -0.0216]],

In [9]:
from tqdm import tqdm
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
import torch.utils.data as data
import torchvision.transforms as transforms

import medmnist
from medmnist import INFO, Evaluator

In [10]:
data_flag = 'retinamnist'
# [tissuemnist, pathmnist, chestmnist, dermamnist, octmnist, 
# pnemoniamnist, retinamnist, breastmnist, bloodmnist, tissuemnist, organamnist, organcmnist, organsmnist]
download = True

NUM_EPOCHS = 10
BATCH_SIZE = 10
lr = 0.005

info = INFO[data_flag]
task = info['task']
n_channels = info['n_channels']
n_classes = len(info['label'])

DataClass = getattr(medmnist, info['python_class'])

In [11]:
from torchvision.transforms.transforms import Resize
# preprocessing
train_transform = transforms.Compose([
    transforms.Resize(224),
    transforms.Lambda(lambda image: image.convert('RGB')),
    torchvision.transforms.AugMix(),
    transforms.ToTensor(),
    transforms.Normalize(mean=[.5], std=[.5])
])
test_transform = transforms.Compose([
    transforms.Resize(224),
    transforms.Lambda(lambda image: image.convert('RGB')),
    transforms.ToTensor(),
    transforms.Normalize(mean=[.5], std=[.5])
])

# load the data
train_dataset = DataClass(split='train', transform=train_transform, download=download)
test_dataset = DataClass(split='test', transform=test_transform, download=download)

# pil_dataset = DataClass(split='train', download=download)

# encapsulate data into dataloader form
train_loader = data.DataLoader(dataset=train_dataset, batch_size=BATCH_SIZE, shuffle=True)
train_loader_at_eval = data.DataLoader(dataset=train_dataset, batch_size=2*BATCH_SIZE, shuffle=False)
test_loader = data.DataLoader(dataset=test_dataset, batch_size=2*BATCH_SIZE, shuffle=False)

Using downloaded and verified file: C:\Users\Dheeraj\.medmnist\retinamnist.npz
Using downloaded and verified file: C:\Users\Dheeraj\.medmnist\retinamnist.npz


In [12]:
print(train_dataset)
print("===================")
print(test_dataset)

Dataset RetinaMNIST of size 28 (retinamnist)
    Number of datapoints: 1080
    Root location: C:\Users\Dheeraj\.medmnist
    Split: train
    Task: ordinal-regression
    Number of channels: 3
    Meaning of labels: {'0': '0', '1': '1', '2': '2', '3': '3', '4': '4'}
    Number of samples: {'train': 1080, 'val': 120, 'test': 400}
    Description: The RetinaMNIST is based on the DeepDRiD challenge, which provides a dataset of 1,600 retina fundus images. The task is ordinal regression for 5-level grading of diabetic retinopathy severity. We split the source training set with a ratio of 9:1 into training and validation set, and use the source validation set as the test set. The source images of 3×1,736×1,824 are center-cropped and resized into 3×28×28.
    License: CC BY 4.0
Dataset RetinaMNIST of size 28 (retinamnist)
    Number of datapoints: 400
    Root location: C:\Users\Dheeraj\.medmnist
    Split: test
    Task: ordinal-regression
    Number of channels: 3
    Meaning of labels: {'

In [14]:
# Define loss function and optimizer
if task == "multi-label, binary-class":
    criterion = nn.BCEWithLogitsLoss()
else:
    criterion = nn.CrossEntropyLoss()
    
optimizer = optim.SGD(model.parameters(), lr=lr, momentum=0.9)

In [31]:
# Train 
NUM_EPOCHS = 2
for epoch in range(NUM_EPOCHS):
    train_correct = 0
    train_total = 0
    test_correct = 0
    test_total = 0
    print('Epoch [%d/%d]'% (epoch+1, NUM_EPOCHS))
    model.train()
    for inputs, targets in tqdm(train_loader):
        inputs, targets = inputs.cuda(), targets.cuda()
        # forward + backward + optimize
        optimizer.zero_grad()
        outputs = model(inputs)
        
        if task == 'multi-label, binary-class':
            targets = targets.to(torch.float32)
            loss = criterion(outputs, targets)
        else:
            targets = targets.squeeze().long()
            loss = criterion(outputs, targets)
        
        loss.backward()
        optimizer.step()
    print('Loss: %.3f', loss.item())

Epoch [1/2]


100%|██████████| 108/108 [01:41<00:00,  1.06it/s]


Loss: %.3f 1.5766963958740234
Epoch [2/2]


100%|██████████| 108/108 [01:19<00:00,  1.36it/s]

Loss: %.3f 1.6354812383651733


In [17]:
# evaluation

def test(split):
    model.eval()
    y_true = torch.tensor([]).cuda()
    y_score = torch.tensor([]).cuda()
    
    data_loader = train_loader_at_eval if split == 'train' else test_loader

    with torch.no_grad():
        for inputs, targets in data_loader:
            inputs, targets = inputs.cuda(), targets.cuda()
            outputs = model(inputs)

            if task == 'multi-label, binary-class':
                targets = targets.to(torch.float32)
                outputs = outputs.softmax(dim=-1)
            else:
                targets = targets.squeeze().long()
                outputs = outputs.softmax(dim=-1)
                targets = targets.float().resize_(len(targets), 1)

            y_true = torch.cat((y_true, targets), 0)
            y_score = torch.cat((y_score, outputs), 0)

        y_true = y_true.cpu().numpy()
        y_score = y_score.detach().cpu().numpy()
        
        evaluator = Evaluator(data_flag, split)
        metrics = evaluator.evaluate(y_score)
    
        print('%s  auc: %.3f  acc:%.3f' % (split, *metrics))

        
print('==> Evaluating ...')
test('train')
test('test')

==> Evaluating ...
train  auc: 0.766  acc:0.507
test  auc: 0.741  acc:0.555


In [32]:
# evaluation

def test(split):
    model.eval()
    y_true = torch.tensor([]).cuda()
    y_score = torch.tensor([]).cuda()
    
    data_loader = train_loader_at_eval if split == 'train' else test_loader

    with torch.no_grad():
        for inputs, targets in data_loader:
            inputs, targets = inputs.cuda(), targets.cuda()
            outputs = model(inputs)

            if task == 'multi-label, binary-class':
                targets = targets.to(torch.float32)
                outputs = outputs.softmax(dim=-1)
            else:
                targets = targets.squeeze().long()
                outputs = outputs.softmax(dim=-1)
                targets = targets.float().resize_(len(targets), 1)

            y_true = torch.cat((y_true, targets), 0)
            y_score = torch.cat((y_score, outputs), 0)

        y_true = y_true.cpu().numpy()
        y_score = y_score.detach().cpu().numpy()
        
        evaluator = Evaluator(data_flag, split)
        metrics = evaluator.evaluate(y_score)
    
        print('%s  auc: %.3f  acc:%.3f' % (split, *metrics))

        
print('==> Evaluating ...')
test('train')
test('test')

==> Evaluating ...
train  auc: 0.501  acc:0.228
test  auc: 0.553  acc:0.228


In [3]:
from torch.utils.data import Dataset, DataLoader
from PIL import Image

In [4]:
class LGGSegmentationDataset(Dataset):
    def __init__(self, root_dir, transform=None, target_transform=None):
        self.root_dir = root_dir
        self.transform = transform
        self.target_transform = target_transform
        self.image_paths = []
        self.mask_paths = []

        # Load all image and mask paths
        for case in os.listdir(root_dir):
            case_dir = os.path.join(root_dir, case)
            if os.path.isdir(case_dir):
                for file in os.listdir(case_dir):
                    if file.endswith('.tif') and not file.endswith('_mask.tif'):
                        self.image_paths.append(os.path.join(case_dir, file))
                        mask_path = os.path.join(case_dir, file.replace('.tif', '_mask.tif'))
                        self.mask_paths.append(mask_path)

    def __len__(self):
        return len(self.image_paths)

    def __getitem__(self, idx):
        img_path = self.image_paths[idx]
        mask_path = self.mask_paths[idx]
        image = Image.open(img_path).convert('RGB')
        mask = Image.open(mask_path).convert('L')  # Mask is a single-channel image

        if self.transform:
            image = self.transform(image)
        if self.target_transform:
            mask = self.target_transform(mask)

        return image, mask


In [5]:
# Define transformations for images and masks
image_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.5, 0.5, 0.5], std=[0.5, 0.5, 0.5])
])

mask_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor()
])

In [6]:
# Print current directory
print(os.getcwd())
# go to one directory outside

os.chdir('..')
print(os.getcwd())

e:\Projects\MRI-Seg-MedViT\MRI-Seg-MedViT\CustomDataset
e:\Projects\MRI-Seg-MedViT\MRI-Seg-MedViT


In [7]:
from sklearn.model_selection import train_test_split

# Load the dataset
root_dir = 'Data\lgg-mri-segmentation'
dataset = LGGSegmentationDataset(root_dir, transform=image_transform, target_transform=mask_transform)


# Split dataset into train, validation, and test sets
train_indices, val_indices = train_test_split(range(len(dataset)), test_size=0.2, random_state=42)
val_indices, test_indices = train_test_split(val_indices, test_size=0.5, random_state=42)

train_dataset = torch.utils.data.Subset(dataset, train_indices)
val_dataset = torch.utils.data.Subset(dataset, val_indices)
test_dataset = torch.utils.data.Subset(dataset, test_indices)

train_loader = DataLoader(train_dataset, batch_size=16, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=16, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=16, shuffle=False)


In [9]:
import torch
import torch.nn as nn
import torch.optim as optim
from CustomDataset.MedViT import MedViT_small as tiny

# Load and modify the model
pretrained_model = tiny()
checkpoint = torch.load('CustomDataset/MedViT_small_im1k.pth')
pretrained_model.load_state_dict(checkpoint['model'])


ModuleNotFoundError: No module named 'utils'

In [31]:
class MedViT_Segmentation(nn.Module):
    def __init__(self, pretrained_model, num_classes):
        super(MedViT_Segmentation, self).__init__()
        self.encoder = nn.Sequential(*list(pretrained_model.children())[:-2])
        self.decoder = nn.Sequential(
        nn.ConvTranspose2d(1024, 512, kernel_size=4, stride=2, padding=1),  # 112x112
        nn.ReLU(),
        nn.ConvTranspose2d(512, 256, kernel_size=4, stride=2, padding=1),   # 224x224
        nn.ReLU(),
        nn.ConvTranspose2d(256, 128, kernel_size=4, stride=2, padding=1),
        nn.ReLU(),
        nn.ConvTranspose2d(128, num_classes, kernel_size=4, stride=2, padding=1)
    )




    def forward(self, x):
        x = self.encoder(x)
        x = self.decoder(x)
        return x


In [32]:
num_classes = 1  # Binary segmentation
model = MedViT_Segmentation(pretrained_model, num_classes).cuda()

# Define loss function and optimizer
criterion = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(model.parameters(), lr=1e-4)

In [33]:
# Training loop
num_epochs = 20
for epoch in range(num_epochs):
    model.train()
    running_loss = 0.0
    for images, masks in train_loader:
        images, masks = images.cuda(), masks.cuda()
        
        optimizer.zero_grad()
        outputs = model(images)
        loss = criterion(outputs, masks)
        loss.backward()
        optimizer.step()
        
        running_loss += loss.item()
    
    print(f'Epoch [{epoch + 1}/{num_epochs}], Loss: {running_loss / len(train_loader)}')
    
    # Validate the model
    model.eval()
    val_loss = 0.0
    with torch.no_grad():
        for images, masks in val_loader:
            images, masks = images.cuda(), masks.cuda()
            outputs = model(images)
            loss = criterion(outputs, masks)
            val_loss += loss.item()
    
    print(f'Validation Loss: {val_loss / len(val_loader)}')



RuntimeError: CUDA error: out of memory
CUDA kernel errors might be asynchronously reported at some other API call, so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.
Compile with `TORCH_USE_CUDA_DSA` to enable device-side assertions.


In [ ]:
# Evaluate the model
model.eval()
test_loss = 0.0
with torch.no_grad():
    for images, masks in test_loader:
        images, masks = images.cuda(), masks.cuda()
        outputs = model(images)
        loss = criterion(outputs, masks)
        test_loss += loss.item()
print(f'Test Loss: {test_loss / len(test_loader)}')
